In [1]:
## This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0302_MR1_mpr-3_154.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0114_MR1_mpr-1_130.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0150_MR1_mpr-3_129.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0253_MR1_mpr-3_113.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0349_MR1_mpr-4_150.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0045_MR1_mpr-2_102.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0209_MR1_mpr-4_128.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0074_MR1_mpr-4_140.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0330_MR1_mpr-4_112.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0234_MR1_mpr-4_113.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0065_MR1_mpr-3_131.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0207_MR1_mpr-2_106.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0375_MR1_mpr-1_136.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0160_MR1_mpr-4_

# Inception-ResNet-V2

In [ ]:
import os
import random
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from PIL import Image
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
from sklearn.utils import class_weight
from sklearn.metrics import classification_report, confusion_matrix
import tensorflow as tf
from tensorflow.keras.applications import InceptionResNetV2
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense, Dropout, BatchNormalization
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau
from tensorflow.keras.optimizers import Adam
from tqdm import tqdm

In [ ]:
# Set seeds for reproducibility
SEED = 42
random.seed(SEED)
np.random.seed(SEED)
tf.random.set_seed(SEED)

In [ ]:
# Parameters
DATA_DIR = '/kaggle/input/imagesoasis/Data'  # Update this path if necessary
CLASSES = ['Non Demented', 'Very mild Dementia', 'Mild Dementia', 'Moderate Dementia']
SAMPLES_PER_CLASS_MAIN = 450  # 450 for training and testing
SAMPLES_PER_CLASS_ADDITIONAL = 15  # 15 for additional testing
IMG_SIZE = 299  # InceptionResNetV2 expects 299x299 images
BATCH_SIZE = 32
EPOCHS = 50

In [ ]:
def sample_images(data_dir, classes, samples_main, samples_additional):
    image_paths_main = []
    labels_main = []
    image_paths_additional = []
    labels_additional = []
    
    for class_name in classes:
        class_dir = os.path.join(data_dir, class_name)
        if not os.path.exists(class_dir):
            print(f"Warning: Directory not found: {class_dir}. Skipping this class.")
            continue
        all_class_images = [
            os.path.join(root, f)
            for root, _, files in os.walk(class_dir)
            for f in files if f.lower().endswith(('.jpg', '.jpeg', '.png'))
        ]
        random.shuffle(all_class_images)
        
        if len(all_class_images) < samples_main + samples_additional:
            raise ValueError(f"Not enough images in {class_name}. Found {len(all_class_images)}, need {samples_main + samples_additional}.")
        
        sampled_main = all_class_images[:samples_main]
        sampled_additional = all_class_images[samples_main:samples_main + samples_additional]
        
        image_paths_main.extend(sampled_main)
        labels_main.extend([class_name]*len(sampled_main))
        
        image_paths_additional.extend(sampled_additional)
        labels_additional.extend([class_name]*len(sampled_additional))
    
    return image_paths_main, labels_main, image_paths_additional, labels_additional

image_paths_main, labels_main, image_paths_additional, labels_additional = sample_images(
    DATA_DIR, CLASSES, SAMPLES_PER_CLASS_MAIN, SAMPLES_PER_CLASS_ADDITIONAL
)

In [ ]:
print("\nImages sampled per class for main dataset:")
for cls in CLASSES:
    count = sum(1 for l in labels_main if l == cls)
    print(f"{cls}: {count}")

print("\nImages sampled per class for additional testing:")
for cls in CLASSES:
    count = sum(1 for l in labels_additional if l == cls)
    print(f"{cls}: {count}")


In [ ]:
def load_and_preprocess(img_path, img_size=IMG_SIZE):
    try:
        img = Image.open(img_path).convert('RGB')
        img = img.resize((img_size, img_size))
        img = np.array(img)
        img = tf.keras.applications.inception_resnet_v2.preprocess_input(img)
        return img
    except Exception as e:
        print(f"Error loading image {img_path}: {e}")
        return None

In [ ]:
# Load and preprocess main dataset
X_main = []
valid_image_paths_main = []
for path in tqdm(image_paths_main, desc="Loading main images"):
    img = load_and_preprocess(path)
    if img is not None:
        X_main.append(img)
        valid_image_paths_main.append(path)
X_main = np.array(X_main)
print("\nMain X shape:", X_main.shape)

In [ ]:
# Load and preprocess additional testing dataset
X_additional = []
valid_image_paths_additional = []
for path in tqdm(image_paths_additional, desc="Loading additional test images"):
    img = load_and_preprocess(path)
    if img is not None:
        X_additional.append(img)
        valid_image_paths_additional.append(path)
X_additional = np.array(X_additional)
print("Additional X shape:", X_additional.shape)

In [ ]:
# Encode main labels
label_encoder = LabelEncoder()
y_int_main = label_encoder.fit_transform(labels_main)
# One-hot encode
y_int_main = y_int_main.reshape(-1,1)
ohe = OneHotEncoder(sparse=False)
y_main = ohe.fit_transform(y_int_main)
print("\nMain y shape:", y_main.shape)
print("Classes:", label_encoder.classes_)

In [ ]:
# Encode additional labels
y_int_additional = label_encoder.transform(labels_additional)
y_int_additional = y_int_additional.reshape(-1,1)
y_additional = ohe.transform(y_int_additional)
print("Additional y shape:", y_additional.shape)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(
    X_main, y_main, test_size=0.2, random_state=SEED, stratify=y_main
)

print(f"\nTraining samples: {X_train.shape[0]}")
print(f"Testing samples: {X_test.shape[0]}")

# Further split training data into train and validation
X_train, X_val, y_train, y_val = train_test_split(
    X_train, y_train, test_size=0.1, random_state=SEED, stratify=y_train
)

print(f"Validation samples: {X_val.shape[0]}")

In [ ]:
y_train_labels = np.argmax(y_train, axis=1)
class_weights_values = class_weight.compute_class_weight(
    class_weight='balanced',
    classes=np.unique(y_train_labels),
    y=y_train_labels
)
class_weights_dict = dict(enumerate(class_weights_values))
print(f"\nClass Weights: {class_weights_dict}")

In [ ]:
base_model = InceptionResNetV2(weights='imagenet', include_top=False, input_shape=(IMG_SIZE, IMG_SIZE, 3))

# Freeze the base model
base_model.trainable = False

# Add custom layers on top of the base model
x = base_model.output
x = GlobalAveragePooling2D()(x)
x = BatchNormalization()(x)  # Added BatchNormalization
x = Dense(1024, activation='relu')(x)
x = Dropout(0.5)(x)
x = Dense(512, activation='relu')(x)
x = Dropout(0.5)(x)
x = Dense(256, activation='relu')(x)  # Added another Dense layer
x = Dropout(0.5)(x)
predictions = Dense(len(CLASSES), activation='softmax')(x)

# Define the complete model
model = Model(inputs=base_model.input, outputs=predictions)

# Compile the model with Adam optimizer and initial learning rate
optimizer = Adam(learning_rate=1e-4)
model.compile(optimizer=optimizer,
              loss='categorical_crossentropy',
              metrics=['accuracy'])

model.summary()

In [ ]:
early_stop = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True, verbose=1)
checkpoint = ModelCheckpoint('best_model.keras', monitor='val_loss', save_best_only=True, verbose=1)
reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.2, patience=5, min_lr=1e-6, verbose=1)

In [ ]:
history = model.fit(
    X_train, y_train,
    validation_data=(X_val, y_val),
    epochs=EPOCHS,
    batch_size=BATCH_SIZE,
    callbacks=[early_stop, checkpoint, reduce_lr],
    class_weight=class_weights_dict,
    shuffle=True
)

In [ ]:
def plot_history(history):
    acc = history.history['accuracy']
    val_acc = history.history['val_accuracy']
    loss = history.history['loss']
    val_loss = history.history['val_loss']
    epochs_range = range(1, len(acc) + 1)
    
    plt.figure(figsize=(14, 6))
    
    # Accuracy Plot
    plt.subplot(1, 2, 1)
    plt.plot(epochs_range, acc, label='Training Accuracy', marker='o')
    plt.plot(epochs_range, val_acc, label='Validation Accuracy', marker='o')
    plt.title('Training and Validation Accuracy')
    plt.xlabel('Epochs')
    plt.ylabel('Accuracy')
    plt.legend(loc='lower right')
    
    # Loss Plot
    plt.subplot(1, 2, 2)
    plt.plot(epochs_range, loss, label='Training Loss', marker='o')
    plt.plot(epochs_range, val_loss, label='Validation Loss', marker='o')
    plt.title('Training and Validation Loss')
    plt.xlabel('Epochs')
    plt.ylabel('Loss')
    plt.legend(loc='upper right')
    
    plt.tight_layout()
    plt.show()

plot_history(history)

In [ ]:
# Unfreeze some layers of the base model for fine-tuning
base_model.trainable = True

# Let's unfreeze the top 100 layers
for layer in base_model.layers[:-100]:
    layer.trainable = False

# Recompile the model with a lower learning rate
optimizer_fine = Adam(learning_rate=1e-5)
model.compile(optimizer=optimizer_fine,
              loss='categorical_crossentropy',
              metrics=['accuracy'])

model.summary()

In [ ]:
fine_tune_history = model.fit(
    X_train, y_train,
    validation_data=(X_val, y_val),
    epochs=EPOCHS,
    batch_size=BATCH_SIZE,
    callbacks=[early_stop, checkpoint, reduce_lr],
    class_weight=class_weights_dict,
    shuffle=True
)

In [ ]:
plot_history(fine_tune_history)

In [ ]:
# Load the best model
model.load_weights('best_model.keras')
print("\nBest model loaded.")


In [ ]:
# Evaluate on test data
test_loss, test_accuracy = model.evaluate(X_test, y_test, batch_size=BATCH_SIZE, verbose=1)
print(f"\nTest Accuracy: {test_accuracy:.4f}")
print(f"Test Loss: {test_loss:.4f}")


In [ ]:
y_pred = model.predict(X_test, batch_size=BATCH_SIZE)
y_pred_labels = np.argmax(y_pred, axis=1)
y_true_labels = np.argmax(y_test, axis=1)

print("\nClassification Report:")
print(classification_report(y_true_labels, y_pred_labels, target_names=CLASSES))

print("Confusion Matrix:")
print(confusion_matrix(y_true_labels, y_pred_labels))

In [ ]:
# Load and preprocess additional images
additional_X = []
for path in tqdm(valid_image_paths_additional, desc="Loading additional test images"):
    img = load_and_preprocess(path)
    if img is not None:
        additional_X.append(img)
additional_X = np.array(additional_X)
print("\nAdditional X shape:", additional_X.shape)

In [ ]:
# Encode additional labels
y_int_additional = label_encoder.transform(labels_additional)
y_additional = ohe.transform(y_int_additional.reshape(-1,1))

In [ ]:
# Predict on additional images
y_additional_pred = model.predict(additional_X, batch_size=1)
y_additional_pred_labels = np.argmax(y_additional_pred, axis=1)
y_additional_true_labels = np.argmax(y_additional, axis=1)


In [ ]:
# Plot the additional test images with predictions
plt.figure(figsize=(20, 15))  # Increased figure size for larger images
images_per_row = 4  # Reduce the number of images per row for larger individual plots
rows = (len(additional_X) + images_per_row - 1) // images_per_row  # Calculate required rows

for i in range(len(additional_X)):
    plt.subplot(rows, images_per_row, i + 1)
    img = additional_X[i]
    # Reverse the preprocess_input for visualization
    img_display = img.copy()
    img_display = (img_display + 1) / 2.0  # InceptionResNetV2 preprocess_input scales input between -1 and 1
    img_display = np.clip(img_display, 0, 1)
    plt.imshow(img_display)
    true_label = label_encoder.classes_[y_additional_true_labels[i]]
    pred_label = label_encoder.classes_[y_additional_pred_labels[i]]
    title_color = 'green' if true_label == pred_label else 'red'
    plt.title(f"True: {true_label}\nPred: {pred_label}", color=title_color, fontsize=12)
    plt.axis('off')

plt.tight_layout()
plt.show()


In [ ]:
# Classification report for additional testing
print("\nAdditional Testing Classification Report:")
print(classification_report(y_additional_true_labels, y_additional_pred_labels, target_names=CLASSES))

print("Additional Testing Confusion Matrix:")
print(confusion_matrix(y_additional_true_labels, y_additional_pred_labels))

# VGG19

In [ ]:
import os
import random
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from PIL import Image
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
from sklearn.utils import class_weight
from sklearn.metrics import classification_report, confusion_matrix
import tensorflow as tf
from tensorflow.keras.applications import VGG19
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense, Dropout, BatchNormalization
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau
from tensorflow.keras.optimizers import Adam
from tqdm import tqdm

In [ ]:
# Set seeds for reproducibility
SEED = 42
random.seed(SEED)
np.random.seed(SEED)
tf.random.set_seed(SEED)

In [ ]:
DATA_DIR = '/kaggle/input/imagesoasis/Data'  
CLASSES = ['Non Demented', 'Very mild Dementia', 'Mild Dementia', 'Moderate Dementia']
SAMPLES_PER_CLASS_MAIN = 450  # 450 for training and testing
SAMPLES_PER_CLASS_ADDITIONAL = 15  # 15 for additional testing
IMG_SIZE = 224  # VGG19 expects 224x224 images
BATCH_SIZE = 32
EPOCHS = 50

In [ ]:
def sample_images(data_dir, classes, samples_main, samples_additional):
    image_paths_main = []
    labels_main = []
    image_paths_additional = []
    labels_additional = []
    
    for class_name in classes:
        class_dir = os.path.join(data_dir, class_name)
        if not os.path.exists(class_dir):
            print(f"Warning: Directory not found: {class_dir}. Skipping this class.")
            continue
        all_class_images = [
            os.path.join(root, f)
            for root, _, files in os.walk(class_dir)
            for f in files if f.lower().endswith(('.jpg', '.jpeg', '.png'))
        ]
        random.shuffle(all_class_images)
        
        if len(all_class_images) < samples_main + samples_additional:
            raise ValueError(f"Not enough images in {class_name}. Found {len(all_class_images)}, need {samples_main + samples_additional}.")
        
        sampled_main = all_class_images[:samples_main]
        sampled_additional = all_class_images[samples_main:samples_main + samples_additional]
        
        image_paths_main.extend(sampled_main)
        labels_main.extend([class_name]*len(sampled_main))
        
        image_paths_additional.extend(sampled_additional)
        labels_additional.extend([class_name]*len(sampled_additional))
    
    return image_paths_main, labels_main, image_paths_additional, labels_additional

image_paths_main, labels_main, image_paths_additional, labels_additional = sample_images(
    DATA_DIR, CLASSES, SAMPLES_PER_CLASS_MAIN, SAMPLES_PER_CLASS_ADDITIONAL
)

In [ ]:
def load_and_preprocess(img_path, img_size=IMG_SIZE):
    try:
        img = Image.open(img_path).convert('RGB')
        img = img.resize((img_size, img_size))
        img = np.array(img)
        img = tf.keras.applications.vgg19.preprocess_input(img)
        return img
    except Exception as e:
        print(f"Error loading image {img_path}: {e}")
        return None

In [ ]:
# Preprocessing and dataset preparation
X_main = []
valid_image_paths_main = []
for path in tqdm(image_paths_main, desc="Loading main images"):
    img = load_and_preprocess(path)
    if img is not None:
        X_main.append(img)
        valid_image_paths_main.append(path)
X_main = np.array(X_main)

X_additional = []
valid_image_paths_additional = []
for path in tqdm(image_paths_additional, desc="Loading additional test images"):
    img = load_and_preprocess(path)
    if img is not None:
        X_additional.append(img)
        valid_image_paths_additional.append(path)
X_additional = np.array(X_additional)

In [ ]:
# Encode labels
label_encoder = LabelEncoder()
y_int_main = label_encoder.fit_transform(labels_main)
ohe = OneHotEncoder(sparse=False)
y_main = ohe.fit_transform(y_int_main.reshape(-1, 1))

y_int_additional = label_encoder.transform(labels_additional)
y_additional = ohe.transform(y_int_additional.reshape(-1, 1))

In [ ]:
# Splitting data
X_train, X_test, y_train, y_test = train_test_split(
    X_main, y_main, test_size=0.2, random_state=SEED, stratify=y_main
)

X_train, X_val, y_train, y_val = train_test_split(
    X_train, y_train, test_size=0.1, random_state=SEED, stratify=y_train
)

In [ ]:
# Class weights
y_train_labels = np.argmax(y_train, axis=1)
class_weights_values = class_weight.compute_class_weight(
    class_weight='balanced',
    classes=np.unique(y_train_labels),
    y=y_train_labels
)
class_weights_dict = dict(enumerate(class_weights_values))

In [ ]:
# Model architecture for VGG19
base_model = VGG19(weights='imagenet', include_top=False, input_shape=(IMG_SIZE, IMG_SIZE, 3))

# Freeze the base model
base_model.trainable = False

# Add custom layers
x = base_model.output
x = GlobalAveragePooling2D()(x)
x = BatchNormalization()(x)
x = Dense(1024, activation='relu')(x)
x = Dropout(0.5)(x)
x = Dense(512, activation='relu')(x)
x = Dropout(0.5)(x)
x = Dense(256, activation='relu')(x)
x = Dropout(0.5)(x)
predictions = Dense(len(CLASSES), activation='softmax')(x)

# Define the model
model = Model(inputs=base_model.input, outputs=predictions)

# Compile the model
optimizer = Adam(learning_rate=1e-4)
model.compile(optimizer=optimizer,
              loss='categorical_crossentropy',
              metrics=['accuracy'])

model.summary()

In [ ]:
# Callbacks
early_stop = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True, verbose=1)
checkpoint = ModelCheckpoint('vgg19_best_model.keras', monitor='val_loss', save_best_only=True, verbose=1)
reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.2, patience=5, min_lr=1e-6, verbose=1)

In [ ]:
# Training
history = model.fit(
    X_train, y_train,
    validation_data=(X_val, y_val),
    epochs=EPOCHS,
    batch_size=BATCH_SIZE,
    callbacks=[early_stop, checkpoint, reduce_lr],
    class_weight=class_weights_dict,
    shuffle=True
)

In [ ]:
# Plot training history
def plot_history(history):
    acc = history.history['accuracy']
    val_acc = history.history['val_accuracy']
    loss = history.history['loss']
    val_loss = history.history['val_loss']
    epochs_range = range(1, len(acc) + 1)
    
    plt.figure(figsize=(14, 6))
    
    plt.subplot(1, 2, 1)
    plt.plot(epochs_range, acc, label='Training Accuracy', marker='o')
    plt.plot(epochs_range, val_acc, label='Validation Accuracy', marker='o')
    plt.title('Training and Validation Accuracy')
    plt.xlabel('Epochs')
    plt.ylabel('Accuracy')
    plt.legend(loc='lower right')
    
    plt.subplot(1, 2, 2)
    plt.plot(epochs_range, loss, label='Training Loss', marker='o')
    plt.plot(epochs_range, val_loss, label='Validation Loss', marker='o')
    plt.title('Training and Validation Loss')
    plt.xlabel('Epochs')
    plt.ylabel('Loss')
    plt.legend(loc='upper right')
    
    plt.tight_layout()
    plt.show()

plot_history(history)

In [ ]:
# Evaluate model on test data
test_loss, test_accuracy = model.evaluate(X_test, y_test, batch_size=BATCH_SIZE, verbose=1)
print(f"\nTest Accuracy: {test_accuracy:.4f}")
print(f"Test Loss: {test_loss:.4f}")

y_pred = model.predict(X_test, batch_size=BATCH_SIZE)
y_pred_labels = np.argmax(y_pred, axis=1)
y_true_labels = np.argmax(y_test, axis=1)

print("\nClassification Report:")
print(classification_report(y_true_labels, y_pred_labels, target_names=CLASSES))

print("Confusion Matrix:")
print(confusion_matrix(y_true_labels, y_pred_labels))


In [ ]:
# Additional 15 random images per class (not included in train/test/val)
additional_image_paths = []
additional_labels = []

for class_name in CLASSES:
    class_dir = os.path.join(DATA_DIR, class_name)
    if not os.path.exists(class_dir):
        print(f"Warning: Directory not found: {class_dir}. Skipping this class.")
        continue
    all_class_images = [
        os.path.join(root, f)
        for root, _, files in os.walk(class_dir)
        for f in files if f.lower().endswith(('.jpg', '.jpeg', '.png'))
    ]
    # Exclude images already used in train/test/val
    used_images = set(image_paths_main) | set(image_paths_additional)
    available_images = [img for img in all_class_images if img not in used_images]
    
    if len(available_images) < SAMPLES_PER_CLASS_ADDITIONAL:
        raise ValueError(f"Not enough images for class {class_name}. Found {len(available_images)}, need {SAMPLES_PER_CLASS_ADDITIONAL}.")
    
    random.shuffle(available_images)
    selected_images = available_images[:SAMPLES_PER_CLASS_ADDITIONAL]
    additional_image_paths.extend(selected_images)
    additional_labels.extend([class_name] * len(selected_images))

In [ ]:
# Preprocess the additional test images
X_additional = []
valid_additional_image_paths = []
for path in tqdm(additional_image_paths, desc="Loading additional images"):
    img = load_and_preprocess(path)
    if img is not None:
        X_additional.append(img)
        valid_additional_image_paths.append(path)
X_additional = np.array(X_additional)

In [ ]:
# Encode additional labels
y_int_additional = label_encoder.transform(additional_labels)
y_additional = ohe.transform(y_int_additional.reshape(-1, 1))

In [ ]:
# Predict on additional test images
y_additional_pred = model.predict(X_additional, batch_size=1)
y_additional_pred_labels = np.argmax(y_additional_pred, axis=1)
y_additional_true_labels = np.argmax(y_additional, axis=1)

In [ ]:
# Plot the additional test images with predictions
plt.figure(figsize=(20, 15))  # Increased figure size for larger images
images_per_row = 4  # Reduce the number of images per row for larger individual plots
rows = (len(X_additional) + images_per_row - 1) // images_per_row  # Calculate required rows

for i in range(len(X_additional)):
    plt.subplot(rows, images_per_row, i + 1)
    img = X_additional[i]
    # Reverse the preprocess_input for visualization
    img_display = img.copy()
    img_display = (img_display + 1) / 2.0  # VGG19 preprocess_input scales input between -1 and 1
    img_display = np.clip(img_display, 0, 1)
    plt.imshow(img_display)
    true_label = label_encoder.classes_[y_additional_true_labels[i]]
    pred_label = label_encoder.classes_[y_additional_pred_labels[i]]
    title_color = 'green' if true_label == pred_label else 'red'
    plt.title(f"True: {true_label}\nPred: {pred_label}", color=title_color, fontsize=12)
    plt.axis('off')

plt.tight_layout()
plt.show()

In [ ]:
# Classification report and confusion matrix for additional testing
print("\nAdditional Testing Classification Report:")
print(classification_report(y_additional_true_labels, y_additional_pred_labels, target_names=CLASSES))

print("Additional Testing Confusion Matrix:")
print(confusion_matrix(y_additional_true_labels, y_additional_pred_labels))
